# Proyecto de selección de APIs

En el presente código a continuación se efectuó la conexión con una API de la página de la ciudad de Nueva York. Más precisamente con los datos demográficos para distintos años de las escuelas públicas de dicha ciudad.

In [12]:
import requests
import json
import pandas as pd

df=requests.get('https://data.cityofnewyork.us/api/views/ihfw-zy9j/rows.json')

print(df)

<Response [200]>


Como se puede observar, obtuvimos el código 200, lo cual implica que nuestro request fue exitoso.
Procedemos luego, a llevar a texto y luego a una visualización de la información en formato Json a fin de luego, poder pasarlo a un dataframe y poder trabajar con la información del database.

In [32]:
print(len(df.text))
df.text

4109813


'{\n  "meta" : {\n    "view" : {\n      "id" : "ihfw-zy9j",\n      "name" : "2006 - 2012 School Demographics and Accountability Snapshot",\n      "assetType" : "dataset",\n      "attribution" : "Department of Education (DOE)",\n      "attributionLink" : "http://schools.nyc.gov/NR/rdonlyres/F318E6F9-5787-403E-8ABD-139656D7A06E/0/DemographicSnapshot2012Public.xlsx",\n      "averageRating" : 0,\n      "category" : "Education",\n      "createdAt" : 1361423719,\n      "description" : "Annual school accounts of NYC public school student populations served by grade, special programs, ethnicity, gender and Title I funded programs.\xa0",\n      "displayType" : "table",\n      "downloadCount" : 6834,\n      "hideFromCatalog" : false,\n      "hideFromDataJson" : false,\n      "indexUpdatedAt" : 1536596810,\n      "newBackend" : true,\n      "numberOfComments" : 1,\n      "oid" : 2581590,\n      "provenance" : "official",\n      "publicationAppendEnabled" : false,\n      "publicationDate" : 136142

In [33]:
texto=df.text
json.loads(texto)

{'meta': {'view': {'id': 'ihfw-zy9j',
   'name': '2006 - 2012 School Demographics and Accountability Snapshot',
   'assetType': 'dataset',
   'attribution': 'Department of Education (DOE)',
   'attributionLink': 'http://schools.nyc.gov/NR/rdonlyres/F318E6F9-5787-403E-8ABD-139656D7A06E/0/DemographicSnapshot2012Public.xlsx',
   'averageRating': 0,
   'category': 'Education',
   'createdAt': 1361423719,
   'description': 'Annual school accounts of NYC public school student populations served by grade, special programs, ethnicity, gender and Title I funded programs.\xa0',
   'displayType': 'table',
   'downloadCount': 6834,
   'hideFromCatalog': False,
   'hideFromDataJson': False,
   'indexUpdatedAt': 1536596810,
   'newBackend': True,
   'numberOfComments': 1,
   'oid': 2581590,
   'provenance': 'official',
   'publicationAppendEnabled': False,
   'publicationDate': 1361423794,
   'publicationGroup': 690411,
   'publicationStage': 'published',
   'rowClass': '',
   'rowsUpdatedAt': 13614

El código a continuación busca eliminar las filas relacionadas a meta data que no aportan al dataset y nos trae errores al intentar pasarlo a un dataframe.

In [34]:
response=requests.get('https://data.cityofnewyork.us/api/views/ihfw-zy9j/rows.json').json()

columns=[]

for i in response['meta']['view']['columns']:

    if(i['dataTypeName']=='meta_data'):

        continue
    else:

        columns.append(i['name'])

De la limpieza efectuada obtuvimos las siguientes columnas:

In [35]:
columns

['DBN',
 'Name',
 'schoolyear',
 'fl_percent',
 'frl_percent',
 'total_enrollment',
 'prek',
 'k',
 'grade1',
 'grade2',
 'grade3',
 'grade4',
 'grade5',
 'grade6',
 'grade7',
 'grade8',
 'grade9',
 'grade10',
 'grade11',
 'grade12',
 'ell_num',
 'ell_percent',
 'sped_num',
 'sped_percent',
 'ctt_num',
 'selfcontained_num',
 'asian_num',
 'asian_per',
 'black_num',
 'black_per',
 'hispanic_num',
 'hispanic_per',
 'white_num',
 'white_per',
 'male_num',
 'male_per',
 'female_num',
 'female_per']

Habiendo detectado las columnas, nos queda ahora alinear las filas correspondientes y en formato Json para su conversión a dataframe:

In [38]:
len(response['data'][0])

46

Identificamos 38 columnas y el dataset tiene 46, ya que los 8 de diferencia están relacionados a meta_data. Con lo cual, más abajo, generamos un loop para que sólo tome la información de las 38 columnas.

In [50]:
count=0

for i in response['data'][0][len(response['data'][0])-len(columns):len(response['data'][0])]: #para los índices 8 a 45

    d[count].append(i)

    count=count+1

In [40]:
d = [[] for x in  range(len(columns))]

In [41]:
for i in response['data']:
    count=0
    for j in  range(len(response['data'][0])-len(columns),len(response['data'][0])):
        d[count].append(i[j])
        count+=1

Hacemos algunas verificaciones para evitar errores futuros.

In [42]:
d[0][0:5]

['01M015', '01M015', '01M015', '01M015', '01M015']

In [43]:
d[1][0:5]

['P.S. 015 ROBERTO CLEMENTE',
 'P.S. 015 ROBERTO CLEMENTE',
 'P.S. 015 ROBERTO CLEMENTE',
 'P.S. 015 ROBERTO CLEMENTE',
 'P.S. 015 ROBERTO CLEMENTE']

In [44]:
d[2][0:5]

['20052006', '20062007', '20072008', '20082009', '20092010']

No hemos identificado ningún desvío a la vista, con lo cual procedemos a convertir el archivo Json en un dataframe.

In [45]:
json_dict={}

for i in  range(0,len(columns)):
	json_dict.update({columns[i]:d[i]})

In [46]:
json_dict.keys()

dict_keys(['DBN', 'Name', 'schoolyear', 'fl_percent', 'frl_percent', 'total_enrollment', 'prek', 'k', 'grade1', 'grade2', 'grade3', 'grade4', 'grade5', 'grade6', 'grade7', 'grade8', 'grade9', 'grade10', 'grade11', 'grade12', 'ell_num', 'ell_percent', 'sped_num', 'sped_percent', 'ctt_num', 'selfcontained_num', 'asian_num', 'asian_per', 'black_num', 'black_per', 'hispanic_num', 'hispanic_per', 'white_num', 'white_per', 'male_num', 'male_per', 'female_num', 'female_per'])

In [47]:
data=pd.DataFrame(json_dict)

Finalmente, realizamos algunos análisis del dataframe.

In [48]:
data.head()

DBN                       Name schoolyear fl_percent frl_percent  \
0  01M015  P.S. 015 ROBERTO CLEMENTE   20052006       89.4        None   
1  01M015  P.S. 015 ROBERTO CLEMENTE   20062007       89.4        None   
2  01M015  P.S. 015 ROBERTO CLEMENTE   20072008       89.4        None   
3  01M015  P.S. 015 ROBERTO CLEMENTE   20082009       89.4        None   
4  01M015  P.S. 015 ROBERTO CLEMENTE   20092010                   96.5   

  total_enrollment prek   k grade1 grade2  ... black_num black_per  \
0              281   15  36     40     33  ...        74      26.3   
1              243   15  29     39     38  ...        68        28   
2              261   18  43     39     36  ...        77      29.5   
3              252   17  37     44     32  ...        75      29.8   
4              208   16  40     28     32  ...        67      32.2   

  hispanic_num hispanic_per white_num white_per male_num male_per female_num  \
0          189         67.3         5       1.8      158     56.2        123   
1          153           63         4       1.6      140     57.6        103   
2          157         60.2         7       2.7      143     54.8        118   
3          149         59.1         7       2.8      149     59.1        103   
4          118         56.7         6       2.9      124     59.6         84   

  female_per  
0       43.8  
1       42.4  
2       45.2  
3       40.9  
4       40.4  

[5 rows x 38 columns]

In [49]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10075 entries, 0 to 10074
Data columns (total 38 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   DBN                10075 non-null  object
 1   Name               10075 non-null  object
 2   schoolyear         10075 non-null  object
 3   fl_percent         8566 non-null   object
 4   frl_percent        4482 non-null   object
 5   total_enrollment   10075 non-null  object
 6   prek               4712 non-null   object
 7   k                  5882 non-null   object
 8   grade1             5881 non-null   object
 9   grade2             5851 non-null   object
 10  grade3             5779 non-null   object
 11  grade4             5741 non-null   object
 12  grade5             5777 non-null   object
 13  grade6             4517 non-null   object
 14  grade7             4203 non-null   object
 15  grade8             4085 non-null   object
 16  grade9             3974 non-null   objec

Conclusión:

Hemos logrado conectar con una API de forma exitosa y obtenido la información para poder trabajarla en dataframe, cumpliendo con la consigna de al menos 20 columnas y 10.000 filas.